# 모듈 로드

In [2]:
import numpy as np
import pandas as pd
import warnings
import gc
from tqdm import tqdm_notebook as tqdm
import lightgbm as lgb
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from sklearn.metrics import roc_auc_score
warnings.filterwarnings("ignore")
gc.enable()

In [3]:
pd.set_option('max_rows', 500)
pd.set_option('max_colwidth', 500)
pd.set_option('max_columns', 500)

# 데이터 로드

In [4]:
train = pd.read_csv('./data/train.csv')
test = pd.read_csv('./data/test.csv')
train.shape, test.shape

((200000, 202), (200000, 201))

In [5]:
col_list = train.columns[2:]

In [6]:
train_0 = train[train.target == 0]
train_1 = train[train.target == 1]

In [7]:
pb_idx = np.load('./data_temp/public_LB.npy')
pv_idx = np.load('./data_temp/private_LB.npy')

In [8]:
test_pb = test.iloc[pb_idx].sort_index().copy()
test_pv = test.iloc[pv_idx].sort_index().copy()

test_real = test_pb.append(test_pv)

# Unique Data

In [8]:
# unique df
unique_df = train[['ID_code']]
for col in tqdm(col_list):
    unique_df[col] = train[col].map(((train[col].value_counts() == 1) * 1).to_dict())

In [14]:
unique_train = train[['ID_code', 'target']]
for col in tqdm(col_list):
    unique_train[col] = np.around(train[col] * unique_df[col], 4)

# 삐꾸 데이터 비교

In [97]:
bbiggu = pd.read_csv('./data_temp/new_bbiggu.csv')

In [98]:
bbiggu_ID_code = bbiggu[(bbiggu.target == 0) & (bbiggu.pred > 0.1)].ID_code
normal_ID_code = bbiggu[(bbiggu.target == 1) & (bbiggu.pred > 0.1)].ID_code
new_ID_code = bbiggu[bbiggu.pred > 0.1].ID_code

In [99]:
bbiggu = train[train.ID_code.isin(bbiggu_ID_code)].copy()
normal = train[train.ID_code.isin(normal_ID_code)].copy()
new_train = train[train.ID_code.isin(new_ID_code)].copy()

In [94]:
unique_root = {}
for col in tqdm(col_list):

    unique_root[col] = set(new_train[col].value_counts()[new_train[col].value_counts() == 3].index)

In [95]:
unique_set = {}
    
for col in tqdm(col_list):
    target_1 = unique_root[col].intersection(set(bbiggu[col].unique()))
    target_0 = unique_root[col].intersection(set(normal[col].unique()))
    
    unique_set[col] = {'target_0': target_0, 'target_1': target_1}

In [ ]:
## for i, _ in enumerate(col_list):
    i = i + 1
    if i % 4 != 0:
        continue
    
    print("showing var_{} ~ var_{}".format(i-4, i-1))
    plt.figure(figsize=(15, 8))

    for j, col in enumerate(col_list[i-4:i]):
        j = j + 1
        
        plt.subplot(2, 2, j)
        sns.distplot(list(unique_set[col]['target_0']), label='t=0', color='b', bins=100)
        sns.distplot(list(unique_set[col]['target_1']), label='t=1', color='r', bins=100)
        plt.legend()
        plt.title(col)
            
    plt.show()

In [79]:
roc_auc_score(bbiggu.target, bbiggu.pred)

0.9116527218981605

In [82]:
roc_auc_score(bbiggu.target, bbiggu.pred)

0.9116595156590153

In [100]:
bbiggu

ID_code  target    var_0    var_1    var_2    var_3    var_4  \
1            train_1       0  11.5006  -4.1473  13.8588   5.3890  12.3622   
3            train_3       0  11.0604  -2.1518   8.9522   7.1957  12.5846   
6            train_6       0  11.8091  -0.0832   9.3494   4.2916  11.1355   
14          train_14       0  13.8080   5.0514  17.2611   8.5120  12.8517   
15          train_15       0   3.9416   2.6562  13.3633   6.8895  12.2806   
33          train_33       0  18.2931   0.6422  14.6849   4.1357  11.7496   
51          train_51       0   8.6005   6.2344   9.1086   7.7384  13.3435   
60          train_60       0   5.7733   0.6536   9.3862   6.2292   9.5133   
74          train_74       0   5.4386   2.4679  10.0766   4.4916  10.8987   
75          train_75       0  16.7218  -3.1693  12.8215   7.9725  12.0685   
76          train_76       0  11.6292   2.7266  15.3545   4.6228   9.9694   
79          train_79       0   6.1618   0.4555   9.5015  11.4378  11.0376   
88          train_88       0  12.9982   3.4437   8.1502   5.4169  11.1099   
90          train_90       0  12.8017  -3.6662  13.0387   6.8645   8.3948   
103        train_103       0   7.6003  -0.5622   7.7383   5.5513   8.7066   
107        train_107       0  10.2968  -3.8800  10.4812   8.1058  11.7263   
110        train_110       0  13.2018   0.2193  13.9407   6.9817  10.2966   
115        train_115       0  11.2580  -0.2003  12.1122   7.2458  11.5988   
116        train_116       0   6.3502   2.1981  12.6468   5.8645  10.9847   
123        train_123       0   9.7306   2.1255  10.2120   8.6436  11.6035   
132        train_132       0   5.1687  -0.4308  13.8327   7.6746  11.7847   
141        train_141       0   7.3621  -0.5262  10.8746  10.1974  11.4604   
145        train_145       0  12.0704 -11.1044   7.6663   8.3891   8.1350   
147        train_147       0   9.3256   1.2479   9.0790   6.6928   8.7818   
171        train_171       0  15.5989  -1.5148   7.6828   6.5529  10.0962   
177        train_177       0   8.0007  -3.4548  13.9965   8.8360   9.1615   
180        train_180       0  13.1245  -9.1658   9.8201   4.9837  10.2160   
193        train_193       0  15.9008  -5.3833  12.2930  10.4229  11.9548   
198        train_198       0  11.9800   3.5063  12.0867   5.5473   8.7255   
206        train_206       0   9.2318  -2.4875   9.7946   5.3479   9.7677   
211        train_211       0  11.6441   2.0594  14.2587   1.4313  11.9772   
212        train_212       0   9.8192   4.2980   9.8485   3.4234  10.9148   
214        train_214       0   8.8795   2.6110  11.5639   5.4618  12.1616   
215        train_215       0  16.2942  -2.3415   6.3402   5.9711   9.0590   
216        train_216       0   8.2883   6.0651  12.3366   5.8885  15.1108   
217        train_217       0  13.3862  -0.7191  12.8446   7.5883  12.8530   
227        train_227       0  12.1862  -0.9615  11.0161   8.3727   7.4746   
230        train_230       0   6.0749  -1.0864   5.2487   7.4444  12.2550   
232        train_232       0   7.7658  -1.8612  11.6420   4.9678   9.3783   
244        train_244       0  12.5944  -4.8738   9.0462   9.1649  14.2014   
261        train_261       0   9.0347  -2.1522   7.2815   6.8423  10.6956   
262        train_262       0   7.0432  -4.7970  14.0738   8.1153  11.6583   
263        train_263       0   8.0040  -1.8511  11.7042   6.1549  11.3613   
285        train_285       0  15.4568  -1.9850   6.0917   7.7919  10.4686   
288        train_288       0  11.3004  -1.4658  11.2480   7.5654  10.8043   
293        train_293       0   5.4351   4.5549  10.6677   3.3404  12.8882   
295        train_295       0   8.9534   4.9881  16.6875   6.3010  11.3361   
296        train_296       0  13.3937  -8.1923  12.0539   7.5772   9.9983   
310        train_310       0  14.7966  -1.6315  13.4686   8.8501  10.8493   
311        train_311       0  11.8797  -0.5781  10.5100   7.3104  10.1453   
312        train_312       0  10.5319  -6.1627   7.5123   8.6936   9.7903   
320      

In [23]:
col = 'var_0'

train_1[col].value_counts().value_counts()

1    16942
2     1443
3       82
4        6
Name: var_0, dtype: int64

In [28]:
col = 'var_0'

train_0.iloc[:70000][col].value_counts().value_counts()

1    36985
2    11008
3     2688
4      598
5       99
6        8
Name: var_0, dtype: int64

In [22]:
train_0[col].value_counts()

1     41175
2     24584
3     13490
4      6542
5      2742
6       958
7       335
8       100
9        24
10        8
11        2
Name: var_0, dtype: int64